Imports necessary libraries: ray, torch, torch.nn, torchvision, torch.utils.data, and Ray Train-specific modules.

In [5]:
!pip install -q ray[default] torch torchvision tqdm ray[train] psutil nvidia-ml-py3

In [ ]:
%pip install -U -q ipywidgets

In [43]:
from cmlextensions.ray_cluster import RayCluster

# Set up the Ray Cluster using CMLExtensions
cluster = RayCluster(num_workers=3, worker_cpu=4, worker_memory=8, worker_nvidia_gpu=1, head_cpu=4, head_memory=8, head_nvidia_gpu=1)
cluster.init()

Starting ray head...
Starting 3 ray workers...

--------------------
Ray cluster started
--------------------

The Ray dashboard is running at
https://734nix0zkpcgc133.goes-ocp-cml.apps.field-team-ocp-01.kcloud.cloudera.com/

To connect to this Ray cluster from this CML Session,
use the following Python code:
  import ray
  ray.init(address='ray://10.254.5.113:10001')



In [48]:
# Option 1: If available in your CMLExtensions version
import ray
import json
ray_address = cluster.get_client_url()
dashboard_url = cluster.get_dashboard_url()
print(f"Dashboard URL : {dashboard_url}")
print(f"RAY ADDRESS : {ray_address}")

ray.init(address=ray_address, allow_multiple=True)

# Save both to a JSON file
connection_info = {
    "ray_address": ray_address,
    "dashboard_url": dashboard_url
}

with open("ray_address.json", "w") as f:
    json.dump(connection_info, f)

print(f"✅ Connected to Ray cluster at {ray_address}")
print(f"📊 Dashboard URL: {dashboard_url}")
print("📄 Connection info saved to ray_address.json")


2025-04-07 12:44:47,065	INFO client_builder.py:244 -- Passing the following kwargs to ray.init() on the server: log_to_driver


Dashboard URL : https://734nix0zkpcgc133.goes-ocp-cml.apps.field-team-ocp-01.kcloud.cloudera.com/
RAY ADDRESS : ray://10.254.5.113:10001
✅ Connected to Ray cluster at ray://10.254.5.113:10001
📊 Dashboard URL: https://734nix0zkpcgc133.goes-ocp-cml.apps.field-team-ocp-01.kcloud.cloudera.com/
📄 Connection info saved to ray_address.json


In [49]:
import os
from typing import Dict
import psutil
import torch
from filelock import FileLock
from torch import nn
from torch.utils.data import DataLoader
from torchvision import datasets, transforms
from torchvision.transforms import Normalize, ToTensor
from tqdm import tqdm
from ray import train, tune
from ray.tune import Tuner
from ray.train import ScalingConfig, get_context
from ray.train.torch import TorchTrainer
from ray.util import get_node_ip_address
from torch.utils.tensorboard import SummaryWriter
import hashlib
import pynvml

In [52]:
def get_dataloaders(batch_size):
    # Transform to normalize the input images
    transform = transforms.Compose([ToTensor(), Normalize((0.28604,), (0.32025,))])

    with FileLock(os.path.expanduser("~/data.lock")):
        # Download training data from open datasets
        training_data = datasets.FashionMNIST(
            root="~/data",
            train=True,
            download=True,
            transform=transform,
        )

        # Download test data from open datasets
        test_data = datasets.FashionMNIST(
            root="~/data",
            train=False,
            download=True,
            transform=transform,
        )

    # Create data loaders
    train_dataloader = DataLoader(training_data, batch_size=batch_size, shuffle=True)
    test_dataloader = DataLoader(test_data, batch_size=batch_size)

    return train_dataloader, test_dataloader


# Model Definition
class NeuralNetwork(nn.Module):
    def __init__(self):
        super(NeuralNetwork, self).__init__()
        self.flatten = nn.Flatten()
        self.linear_relu_stack = nn.Sequential(
            nn.Linear(28 * 28, 512),
            nn.ReLU(),
            nn.Dropout(0.25),
            nn.Linear(512, 512),
            nn.ReLU(),
            nn.Dropout(0.25),
            nn.Linear(512, 10),
            nn.ReLU(),
        )

    def forward(self, x):
        x = self.flatten(x)
        logits = self.linear_relu_stack(x)
        return logits


def train_func_per_worker(config: Dict):
    
    # Log the node details
    node_ip = get_node_ip_address()
    context = ray.train.get_context()
    node_id = ray.get_runtime_context().node_id.hex()
    rank = context.get_world_rank()
    print(f"[Worker Init] Running on Node ID: {node_id}, IP: {node_ip} worker rank : {rank}")

    # ensuring it sees GPUs
    device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
    # gpu_id = torch.cuda.current_device() if torch.cuda.is_available() else "N/A"

    # Initialize NVML
    pynvml.nvmlInit()
    visible_devices = os.environ.get("CUDA_VISIBLE_DEVICES", "0")
    gpu_id = int(visible_devices.split(",")[0])  # usually just one GPU per worker
    handle = pynvml.nvmlDeviceGetHandleByIndex(gpu_id)
    print(f"[DEBUG] Worker running on node {ray.get_runtime_context().node_id.hex()} using device {device} (GPU ID: {gpu_id})")

    
    # Each Ray worker usually gets assigned a specific GPU
    # Use CUDA_VISIBLE_DEVICES to figure it out
    cuda_visible = os.environ.get("CUDA_VISIBLE_DEVICES", "0")
    gpu_index = int(cuda_visible.split(",")[0])  # take first assigned GPU index
    # Get NVML handle for this GPU
    handle = pynvml.nvmlDeviceGetHandleByIndex(gpu_index)
    
    #let us set up Tensor Board
    rank = context.get_world_rank()
    ray_result_root = os.environ.get("RAY_RESULT_DIR", "/home/cdsw/ray_results")
    experiment_name = "tb_logs"
    writer_logdir = os.path.join(ray_result_root, experiment_name, f"worker_{rank}")
    os.makedirs(writer_logdir, exist_ok=True)

    writer = SummaryWriter(log_dir=writer_logdir)
    print(f"[TensorBoard] Logging to: {writer_logdir}")
    
    lr = config["lr"]
    epochs = config["epochs"]
    batch_size = config["batch_size_per_worker"]

    # Get dataloaders inside the worker training function
    train_dataloader, test_dataloader = get_dataloaders(batch_size=batch_size)

    # [1] Prepare Dataloader for distributed training
    # Shard the datasets among workers and move batches to the correct device
    # =======================================================================
    train_dataloader = ray.train.torch.prepare_data_loader(train_dataloader)
    test_dataloader = ray.train.torch.prepare_data_loader(test_dataloader)

    model = NeuralNetwork()

    # [2] Prepare and wrap your model with DistributedDataParallel
    # Move the model to the correct GPU/CPU device
    # ============================================================
    model = ray.train.torch.prepare_model(model)

    loss_fn = nn.CrossEntropyLoss()
    optimizer = torch.optim.SGD(model.parameters(), lr=lr, momentum=0.9)

    # Function to generate checksum of model weights
    def model_checksum(model):
        combined = b"".join([p.detach().cpu().numpy().tobytes() for p in model.parameters()])
        return hashlib.md5(combined).hexdigest()

    
    # Model training loop
    for epoch in range(epochs):
        if ray.train.get_context().get_world_size() > 1:
            # Required for the distributed sampler to shuffle properly across epochs.
            train_dataloader.sampler.set_epoch(epoch)

        model.train()
        # for X, y in tqdm(train_dataloader, desc=f"[Rank {rank}] Train Epoch {epoch}"):
        for batch_idx, (X, y) in enumerate(tqdm(train_dataloader, desc=f"[Rank {rank}] Train Epoch {epoch}")):

            pred = model(X)
            loss = loss_fn(pred, y)

            optimizer.zero_grad()
            loss.backward()
            optimizer.step()
            
            # --- Per-batch GPU Logging ---
            if torch.cuda.is_available():
                gpu_mem_allocated = torch.cuda.memory_allocated() / 1024**2  # MB
                gpu_mem_reserved = torch.cuda.memory_reserved() / 1024**2
                gpu_utilization = pynvml.nvmlDeviceGetUtilizationRates(handle).gpu  # %

                global_step = epoch * len(train_dataloader) + batch_idx

                writer.add_scalar("Train/GPU/Memory Allocated (MB)", gpu_mem_allocated, global_step)
                writer.add_scalar("Train/GPU/Memory Reserved (MB)", gpu_mem_reserved, global_step)
                writer.add_scalar("Train/GPU/Utilization (%)", gpu_utilization, global_step)
        
            print(f"[GPU LOG] Epoch {epoch}, Batch {batch_idx} | Mem: {gpu_mem_allocated:.2f}MB, Util: {gpu_utilization}%  global_step : {global_step}")

        model.eval()
        test_loss, num_correct, num_total = 0, 0, 0
        with torch.no_grad():
            for X, y in tqdm(test_dataloader, desc=f"[Rank {rank}] Test Epoch {epoch}"):
                pred = model(X)
                loss = loss_fn(pred, y)

                test_loss += loss.item()
                num_total += y.shape[0]
                num_correct += (pred.argmax(1) == y).sum().item()

        test_loss /= len(test_dataloader)
        accuracy = num_correct / num_total
        checksum = model_checksum(model)
        
        # Log metrics to TensorBoard
        writer.add_scalar("Loss/test", test_loss, epoch)
        writer.add_scalar("Accuracy/test", accuracy, epoch)
        writer.add_scalar("ModelChecksum", int(checksum[:8], 16), epoch)  # Log first 8 hex chars as int
        writer.add_text("Node Info", f"Epoch {epoch} - Rank: {rank}, Node: {node_id}", epoch)
    
        # Log sync info (just once per epoch per rank)
        print(f"[Rank {rank}] Epoch {epoch} | Loss: {test_loss:.4f}, Acc: {accuracy:.4f}, Model Checksum: {checksum}")


        # [3] Report metrics to Ray Train
        # ===============================
        # ray.train.report(metrics={"loss": test_loss, "accuracy": accuracy})
        # Log sync info (just once per epoch per rank)
        print(f"[ NodeId {node_id} Rank {rank}] Epoch {epoch} | Loss: {test_loss:.4f}, Acc: {accuracy:.4f}, Model Checksum: {checksum}")

        # ray.train.report(metrics={
        # "loss": test_loss,
        # "accuracy": accuracy,
        # "epoch": epoch,
        # "node_id": node_id,
        # "rank": rank,
        ray.train.report(metrics={
            "loss": test_loss,
            "accuracy": accuracy,
            "epoch": epoch,
            "node_id": node_id,
            "rank": rank,
            "model_checksum": checksum,
            "gpu_utilization": gpu_utilization,
            "gpu_mem_alloc": gpu_mem_allocated,
        })

    #close logging Tensor Board
    writer.close()

def train_fashion_mnist(num_workers=2, use_gpu=False):
    global_batch_size = 32

    train_config = {
        "lr": 1e-3,
        "epochs": 10,
        "batch_size_per_worker": global_batch_size // num_workers,
    }

    # Configure computation resources
    scaling_config = ScalingConfig(num_workers=num_workers, use_gpu=use_gpu)

    # Initialize a Ray TorchTrainer
    trainer = TorchTrainer(
        train_loop_per_worker=train_func_per_worker,
        train_loop_config=train_config,
        scaling_config=scaling_config,
    )

    # [4] Start distributed training
    # Run `train_func_per_worker` on all workers
    # =============================================
    result = trainer.fit()
    print(f"Training result: {result}")
 

In [53]:
# Connect to the existing Ray cluster
train_fashion_mnist(num_workers=3, use_gpu=True)

(TunerInternal pid=767) AIR_VERBOSITY is set, ignoring passed-in ProgressReporter for now.


(TunerInternal pid=767) 
(TunerInternal pid=767) View detailed results here: /home/cdsw/ray_results/TorchTrainer_2025-04-07_12-47-50
(TunerInternal pid=767) To visualize your results with TensorBoard, run: `tensorboard --logdir /tmp/ray/session_2025-04-07_12-40-53_203395_177/artifacts/2025-04-07_12-48-49/TorchTrainer_2025-04-07_12-47-50/driver_artifacts`
(TunerInternal pid=767) 
(TunerInternal pid=767) Training started with configuration:
(TunerInternal pid=767) ╭─────────────────────────────────────────────────╮
(TunerInternal pid=767) │ Training config                                 │
(TunerInternal pid=767) ├─────────────────────────────────────────────────┤
(TunerInternal pid=767) │ train_loop_config/batch_size_per_worker      10 │
(TunerInternal pid=767) │ train_loop_config/epochs                     10 │
(TunerInternal pid=767) │ train_loop_config/lr                      0.001 │
(TunerInternal pid=767) ╰─────────────────────────────────────────────────╯


(TrainTrainable pid=520, ip=10.254.7.94) Trainable.setup took 12.573 seconds. If your trainable is slow to initialize, consider setting reuse_actors=True to reduce actor creation overheads.
(RayTrainWorker pid=604, ip=10.254.7.94) Setting up process group for: env:// [rank=0, world_size=3]
(TorchTrainer pid=520, ip=10.254.7.94) Started distributed worker processes: 
(TorchTrainer pid=520, ip=10.254.7.94) - (node_id=f94cfd48e881a8ef0b964a8593da4b704a1574ca224f294a4cfe1791, ip=10.254.7.94, pid=604) world_rank=0, local_rank=0, node_rank=0
(TorchTrainer pid=520, ip=10.254.7.94) - (node_id=d78b974282fa0fa2bddc3a93a3217bbba8df4be1998f6b20ec83243d, ip=10.254.12.140, pid=398) world_rank=1, local_rank=0, node_rank=1
(TorchTrainer pid=520, ip=10.254.7.94) - (node_id=8132e66e3928a4b82addde0aa19309709a58e788e1dcddeaab904191, ip=10.254.6.117, pid=401) world_rank=2, local_rank=0, node_rank=2
(RayTrainWorker pid=401, ip=10.254.6.117) /tmp/ipykernel_6887/3908580450.py:56: RayDeprecationWarning: This A

(RayTrainWorker pid=401, ip=10.254.6.117) [Worker Init] Running on Node ID: 8132e66e3928a4b82addde0aa19309709a58e788e1dcddeaab904191, IP: 10.254.6.117 worker rank : 2
(RayTrainWorker pid=401, ip=10.254.6.117) [DEBUG] Worker running on node 8132e66e3928a4b82addde0aa19309709a58e788e1dcddeaab904191 using device cuda (GPU ID: 0)
(RayTrainWorker pid=604, ip=10.254.7.94) [Worker Init] Running on Node ID: f94cfd48e881a8ef0b964a8593da4b704a1574ca224f294a4cfe1791, IP: 10.254.7.94 worker rank : 0
(RayTrainWorker pid=604, ip=10.254.7.94) [DEBUG] Worker running on node f94cfd48e881a8ef0b964a8593da4b704a1574ca224f294a4cfe1791 using device cuda (GPU ID: 0)
(RayTrainWorker pid=398, ip=10.254.12.140) [Worker Init] Running on Node ID: d78b974282fa0fa2bddc3a93a3217bbba8df4be1998f6b20ec83243d, IP: 10.254.12.140 worker rank : 1
(RayTrainWorker pid=398, ip=10.254.12.140) [DEBUG] Worker running on node d78b974282fa0fa2bddc3a93a3217bbba8df4be1998f6b20ec83243d using device cuda (GPU ID: 0)
(RayTrainWorker pid

(RayTrainWorker pid=398, ip=10.254.12.140) Moving model to device: cuda:0
(RayTrainWorker pid=398, ip=10.254.12.140) Wrapping provided model in DistributedDataParallel.
(RayTrainWorker pid=604, ip=10.254.7.94) Moving model to device: cuda:0
(RayTrainWorker pid=604, ip=10.254.7.94) Wrapping provided model in DistributedDataParallel.
(RayTrainWorker pid=401, ip=10.254.6.117) Moving model to device: cuda:0
(RayTrainWorker pid=401, ip=10.254.6.117) Wrapping provided model in DistributedDataParallel.
[Rank 0] Train Epoch 0:   0%|          | 2/2000 [00:04<57:52,  1.74s/it]  


...

[Rank 2] Test Epoch 9: 100%|██████████| 334/334 [00:01<00:00, 302.90it/s]


(RayTrainWorker pid=604, ip=10.254.7.94) [Rank 0] Epoch 9 | Loss: 0.3358, Acc: 0.8776, Model Checksum: e8f42bd92533c342a79447a789c2dbc5
(RayTrainWorker pid=604, ip=10.254.7.94) [ NodeId f94cfd48e881a8ef0b964a8593da4b704a1574ca224f294a4cfe1791 Rank 0] Epoch 9 | Loss: 0.3358, Acc: 0.8776, Model Checksum: e8f42bd92533c342a79447a789c2dbc5
(RayTrainWorker pid=401, ip=10.254.6.117) [Rank 2] Epoch 9 | Loss: 0.3175, Acc: 0.8839, Model Checksum: e8f42bd92533c342a79447a789c2dbc5
(RayTrainWorker pid=401, ip=10.254.6.117) [ NodeId 8132e66e3928a4b82addde0aa19309709a58e788e1dcddeaab904191 Rank 2] Epoch 9 | Loss: 0.3175, Acc: 0.8839, Model Checksum: e8f42bd92533c342a79447a789c2dbc5
(RayTrainWorker pid=398, ip=10.254.12.140) [Rank 1] Epoch 9 | Loss: 0.3534, Acc: 0.8743, Model Checksum: e8f42bd92533c342a79447a789c2dbc5
(RayTrainWorker pid=398, ip=10.254.12.140) [ NodeId d78b974282fa0fa2bddc3a93a3217bbba8df4be1998f6b20ec83243d Rank 1] Epoch 9 | Loss: 0.3534, Acc: 0.8743, Model Checksum: e8f42bd92533c342

[Rank 1] Test Epoch 9: 100%|██████████| 334/334 [00:01<00:00, 326.26it/s]


(TunerInternal pid=767) 
(TunerInternal pid=767) Training completed after 10 iterations at 2025-04-07 12:57:58. Total running time: 9min 8s
(TunerInternal pid=767) 
Training result: Result(
  metrics={'loss': 0.3358377871664051, 'accuracy': 0.877624475104979, 'epoch': 9, 'node_id': 'f94cfd48e881a8ef0b964a8593da4b704a1574ca224f294a4cfe1791', 'rank': 0, 'model_checksum': 'e8f42bd92533c342a79447a789c2dbc5', 'gpu_utilization': 64, 'gpu_mem_alloc': 26.50244140625},
  path='/home/cdsw/ray_results/TorchTrainer_2025-04-07_12-47-50/TorchTrainer_a71c6_00000_0_2025-04-07_12-48-50',
  filesystem='local',
  checkpoint=None
)


(TunerInternal pid=767) Wrote the latest version of all result files and experiment state to '/home/cdsw/ray_results/TorchTrainer_2025-04-07_12-47-50' in 4.7144s.


In [42]:
cluster.terminate()

# or 
# Shutdown Ray programmatically
ray.shutdown()